<a href="https://colab.research.google.com/github/san9roy/Space-Telemetry-for-LEO-Satellites/blob/main/Telemetry_Dashboard.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [15]:
# ============================================================
# Telemetry DASHBOARD
# Plotly interactive figures + summary metrics + event tables
# ============================================================

In [16]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import plotly.io as pio
from IPython.display import display

pio.renderers.default = "colab"  # ensures Plotly renders in Colab

In [17]:
# -----------------------------
# 1) Load dataset
# -----------------------------
CSV_PATH = "synthetic_satellite_telemetry.csv"  # change if needed

df = pd.read_csv(CSV_PATH, index_col=0, parse_dates=True).sort_index()

# Make sure core columns exist (so dashboard doesn't break)
expected = [
    "sunlit", "in_view", "comm_ok", "label_gt",
    "voltage_raw", "voltage_filt",
    "temp_raw", "temp_filt",
    "linkq_raw_db", "linkq_filt_db",
    "anomaly_rule", "anomaly_iforest",
    "soc_true", "current_A_true", "if_score"
]
for c in expected:
    if c not in df.columns:
        df[c] = np.nan

# Normalize boolean-ish columns
for b in ["sunlit", "in_view", "comm_ok", "label_gt", "anomaly_rule", "anomaly_iforest"]:
    df[b] = df[b].fillna(0).astype(int)

In [18]:
# -----------------------------
# 2) Helper functions
# -----------------------------
def classification_metrics(gt: np.ndarray, pred: np.ndarray) -> dict:
    gt = gt.astype(int)
    pred = pred.astype(int)
    tp = int(((pred == 1) & (gt == 1)).sum())
    fp = int(((pred == 1) & (gt == 0)).sum())
    fn = int(((pred == 0) & (gt == 1)).sum())
    tn = int(((pred == 0) & (gt == 0)).sum())
    precision = tp / (tp + fp) if (tp + fp) else 0.0
    recall = tp / (tp + fn) if (tp + fn) else 0.0
    f1 = 2 * precision * recall / (precision + recall) if (precision + recall) else 0.0
    return {"tp": tp, "fp": fp, "fn": fn, "tn": tn, "precision": precision, "recall": recall, "f1": f1}


def extract_events(df_: pd.DataFrame, flag_col: str, min_len: int = 10) -> pd.DataFrame:
    """
    Cluster consecutive 1's into anomaly events.
    """
    flags = df_[flag_col].fillna(0).astype(int).to_numpy()
    n = len(flags)

    events = []
    in_event = False
    start_i = None

    for i in range(n):
        if flags[i] == 1 and not in_event:
            in_event = True
            start_i = i

        if in_event and (flags[i] == 0 or i == n - 1):
            end_i = i - 1 if flags[i] == 0 else i
            n_samples = end_i - start_i + 1

            if n_samples >= min_len:
                start_t = df_.index[start_i]
                end_t = df_.index[end_i]
                duration_s = (end_t - start_t).total_seconds()
                events.append([start_t, end_t, duration_s, n_samples])

            in_event = False

    return pd.DataFrame(events, columns=["start", "end", "duration_s", "n_samples"]).sort_values("start")


def add_line(fig, x, y, name):
    fig.add_trace(go.Scatter(x=x, y=y, mode="lines", name=name))


def add_markers(fig, x, mask: np.ndarray, name: str, y_value: float):
    mask = np.asarray(mask).astype(bool)
    if mask.sum() == 0:
        return
    fig.add_trace(
        go.Scatter(
            x=x[mask],
            y=np.full(mask.sum(), y_value),
            mode="markers",
            name=name,
            marker=dict(symbol="x", size=8),
        )
    )


def add_flag_ticks(fig, x, mask: np.ndarray, name: str, y_value: float):
    mask = np.asarray(mask).astype(bool)
    if mask.sum() == 0:
        return
    fig.add_trace(
        go.Scatter(
            x=x[mask],
            y=np.full(mask.sum(), y_value),
            mode="markers",
            name=name,
            marker=dict(symbol="line-ns-open", size=14),
        )
    )


def build_figure(df_: pd.DataFrame, title: str, y_label: str, raw_col: str, filt_col: str) -> go.Figure:
    x = df_.index
    fig = go.Figure()

    # Signals
    add_line(fig, x, df_[raw_col], raw_col)
    add_line(fig, x, df_[filt_col], filt_col)

    # Marker levels
    y_f = df_[filt_col].to_numpy()
    valid = np.isfinite(y_f)
    y_max = float(np.nanmax(y_f[valid])) if valid.any() else 1.0
    y_min = float(np.nanmin(y_f[valid])) if valid.any() else 0.0

    # Anomaly overlays
    add_markers(fig, x, df_["label_gt"].to_numpy() == 1, "GT anomaly", y_max)
    add_markers(fig, x, df_["anomaly_rule"].to_numpy() == 1, "Rule anomaly", y_max)
    add_markers(fig, x, df_["anomaly_iforest"].to_numpy() == 1, "IForest anomaly", y_max)

    # Context overlays (ticks near bottom)
    bottom = y_min - 0.08 * (abs(y_min) + 1.0)
    add_flag_ticks(fig, x, df_["sunlit"].to_numpy() == 1, "sunlit", bottom)
    bottom -= 0.06 * (abs(y_min) + 1.0)
    add_flag_ticks(fig, x, df_["in_view"].to_numpy() == 1, "in_view", bottom)
    bottom -= 0.06 * (abs(y_min) + 1.0)
    missed = (df_["in_view"].to_numpy() == 1) & (df_["comm_ok"].to_numpy() == 0)
    add_flag_ticks(fig, x, missed, "missed_pkt_in_view", bottom)

    fig.update_layout(
        title=title,
        xaxis_title="Time",
        yaxis_title=y_label,
        height=420,
        margin=dict(l=40, r=20, t=60, b=40),
        legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="left", x=0),
    )
    return fig

In [19]:
# -----------------------------
# 3) Summary metrics
# -----------------------------
# Evaluate on in_view only (you can change this to full timeline)
eval_mask = (df["in_view"] == 1)

gt = df.loc[eval_mask, "label_gt"].to_numpy()
rule_pred = df.loc[eval_mask, "anomaly_rule"].to_numpy()
if_pred = df.loc[eval_mask, "anomaly_iforest"].to_numpy()

rule_m = classification_metrics(gt, rule_pred)
if_m = classification_metrics(gt, if_pred)

in_view = (df["in_view"] == 1)
missed = in_view & (df["comm_ok"] == 0)
miss_rate_in_view = missed.sum() / in_view.sum() if in_view.sum() else 0.0

print("=== Dashboard Summary ===")
print(f"Total samples: {len(df):,}")
print(f"In-view samples: {int(in_view.sum()):,}")
print(f"GT anomaly rate (in_view): {gt.mean():.3f} ({gt.mean()*100:.1f}%)")
print(f"Missed packets in view: {int(missed.sum()):,}  |  Miss rate in view: {miss_rate_in_view*100:.2f}%")
print()
print("Rule-based metrics (in_view):", {k: (round(v,3) if isinstance(v,float) else v) for k,v in rule_m.items()})
print("IForest metrics (in_view):    ", {k: (round(v,3) if isinstance(v,float) else v) for k,v in if_m.items()})


=== Dashboard Summary ===
Total samples: 17,280
In-view samples: 4,512
GT anomaly rate (in_view): 0.136 (13.6%)
Missed packets in view: 107  |  Miss rate in view: 2.37%

Rule-based metrics (in_view): {'tp': 565, 'fp': 2652, 'fn': 47, 'tn': 1248, 'precision': 0.176, 'recall': 0.923, 'f1': 0.295}
IForest metrics (in_view):     {'tp': 317, 'fp': 1336, 'fn': 295, 'tn': 2564, 'precision': 0.192, 'recall': 0.518, 'f1': 0.28}


In [20]:
# -----------------------------
# 4) Figures
# -----------------------------
fig_v = build_figure(df, "Battery Pack Voltage", "V", "voltage_raw", "voltage_filt")
fig_t = build_figure(df, "Temperature", "°C", "temp_raw", "temp_filt")
fig_l = build_figure(df, "Link Quality (SNR/RSSI proxy)", "dB", "linkq_raw_db", "linkq_filt_db")

display(fig_v)
display(fig_t)
display(fig_l)


In [21]:
# -----------------------------
# 5) Event tables
# -----------------------------
MIN_EVENT_LEN = 10  # consecutive samples required to form an event (tune as needed)

print("\n=== Clustered Anomaly Events (first 15 rows) ===")

ev_gt = extract_events(df, "label_gt", min_len=MIN_EVENT_LEN)
ev_rule = extract_events(df, "anomaly_rule", min_len=MIN_EVENT_LEN)
ev_if = extract_events(df, "anomaly_iforest", min_len=MIN_EVENT_LEN)

print("\nGT events:")
display(ev_gt.head(15))

print("\nRule events:")
display(ev_rule.head(15))

print("\nIForest events:")
display(ev_if.head(15))



=== Clustered Anomaly Events (first 15 rows) ===

GT events:


start                 end  duration_s  n_samples
0 2026-01-01 14:24:00 2026-01-01 16:47:50      8630.0        864
1 2026-01-02 02:24:00 2026-01-02 05:16:30     10350.0       1036
2 2026-01-02 10:33:30 2026-01-02 11:59:40      5170.0        518


Rule events:


start                 end  duration_s  n_samples
0  2026-01-01 00:10:50 2026-01-01 00:16:40       350.0         36
1  2026-01-01 01:40:50 2026-01-01 01:45:10       260.0         27
2  2026-01-01 02:04:20 2026-01-01 02:07:50       210.0         22
3  2026-01-01 03:10:50 2026-01-01 03:16:20       330.0         34
4  2026-01-01 03:34:20 2026-01-01 03:38:30       250.0         26
5  2026-01-01 04:40:50 2026-01-01 04:46:00       310.0         32
6  2026-01-01 05:04:20 2026-01-01 05:08:00       220.0         23
7  2026-01-01 06:10:50 2026-01-01 06:17:30       400.0         41
8  2026-01-01 06:34:20 2026-01-01 06:38:10       230.0         24
9  2026-01-01 07:40:50 2026-01-01 07:46:10       320.0         33
10 2026-01-01 08:04:20 2026-01-01 08:08:40       260.0         27
11 2026-01-01 09:10:50 2026-01-01 09:16:10       320.0         33
12 2026-01-01 09:34:20 2026-01-01 09:38:10       230.0         24
13 2026-01-01 10:40:50 2026-01-01 10:45:20       270.0         28
14 2026-01-01 11:04:20 2026-01-01 11:08:10       230.0         24


IForest events:


start                 end  duration_s  n_samples
0  2026-01-01 00:00:00 2026-01-01 00:48:00      2880.0        289
1  2026-01-01 01:18:10 2026-01-01 02:10:30      3140.0        315
2  2026-01-01 03:00:00 2026-01-01 03:38:50      2330.0        234
3  2026-01-01 04:30:00 2026-01-01 05:07:50      2270.0        228
4  2026-01-01 06:10:50 2026-01-01 06:23:30       760.0         77
5  2026-01-01 06:23:50 2026-01-01 06:37:00       790.0         80
6  2026-01-01 07:40:50 2026-01-01 07:50:40       590.0         60
7  2026-01-01 08:01:10 2026-01-01 08:06:10       300.0         31
8  2026-01-01 09:10:50 2026-01-01 09:16:10       320.0         33
9  2026-01-01 09:26:40 2026-01-01 09:36:00       560.0         57
10 2026-01-01 10:40:50 2026-01-01 10:44:50       240.0         25
11 2026-01-01 10:59:10 2026-01-01 11:05:40       390.0         40
12 2026-01-01 12:10:50 2026-01-01 12:14:50       240.0         25
13 2026-01-01 12:30:40 2026-01-01 12:35:20       280.0         29
14 2026-01-01 13:40:50 2026-01-01 13:44:10       200.0         21